<a href="https://colab.research.google.com/github/jaimebaldeon/TSP-evolutionary-algorithm/blob/main/TSP.ipynb" target="_parent"><img src="https://colab.research.google.com/assets/colab-badge.svg" alt="Open In Colab"/></a>

In [20]:
import numpy as np
import statistics
import random

class TSP:
  def __init__(self, matrix):
    #self.vertices = [n for n in range(1, numVertices+1)] #to accomplish natural values for vertices
    self.vertices = [n for n in range(matrix[0].size)]  # vertices from 0 to 28
    self.distanceMatrix = matrix

class Individual:
  def __init__(self, tsp):
    self.order = np.random.permutation(tsp.vertices)
    self.α = 0.05

def fitness(tsp, ind):
  value = 0
  ii = 0
  for i in ind.order:
    # Sum up total distance for the individual's sequence of nodes 
    while (ii < ind.order.size - 1):
      pairVertices = ind.order[ii:ii+2]
      value += tsp.distanceMatrix[pairVertices[0], pairVertices[1]]
      ii += 1 
  # add the distance between first and last node
  value += tsp.distanceMatrix[ind.order[-1], ind.order[0]]
  return value

def optimize(tsp):
  λ = 2000 # population size
  μ = 200 # offspring size
  iter =20

  # Initialization
  population = initialize(tsp,λ)
  offspring = []

  # Print initial Candidate solutions
  '''for ind in population:
    print("Candidate solution:  ", ind.order)'''

  # Print initial Population evaluation
  fitnesses = [fitness(tsp, ind) for ind in population]
  print("\nMean fitness:  ", statistics.mean(fitnesses))
  print("Best fitness:  ", min(fitnesses))

  for i in range(iter):
    # Recombination
    for ind in range(μ):
      # Selection
      parent1 = selection(tsp, population)
      parent2 = selection(tsp, population)
      offspring.append(recombination(parent1, parent2))
      mutate(offspring[ind])

    # Mutation
    for ind in population:
      mutate(ind)    

    # Elimination
    population = elimination(population, offspring, tsp)

    fitnesses = [fitness(tsp, ind) for ind in population]
    print(f'---------------------------------  ITERATION {i} ---------------------------------')
    print("Mean fitness:  ", statistics.mean(fitnesses))
    print("Best fitness:  ", min(fitnesses))

  # Print final Candidate solutions
  '''for ind in population:
    print("Candidate solution:  ", ind.order)
    print("Candidate mutation probability:  ", ind.α)'''


def initialize(tsp, λ):
  population = []
  for i in range(λ):
    population.append(Individual(tsp))
  return population

def mutate(individual):
  if np.random.rand() < individual.α:
    i = random.randrange(len(individual.order))
    j = random.randrange(len(individual.order))
    if i < j:
      individual.order[i:j] = individual.order[i:j][::-1]
    else:
      individual.order[j:i] = individual.order[j:i][::-1]

def recombination(parent1, parent2):
  child = parent1
  # Select crossover points randomly
  i = random.randrange(len(parent1.order))
  j = random.randrange(len(parent1.order))
  # Perform order crossover recombination to create the child's order
  if i < j:  
    child.order = order_crossover(parent1.order, parent2.order, i, j)
  else:  
    child.order = order_crossover(parent1.order, parent2.order, j, i)  
  # Set child parameters
  β = 2 * np.random.rand() - 0.5 # coefficient between (-0.5, 1.5)
  child.α = parent1.α + β * (parent2.α - parent1.α)
  return child

def order_crossover(parent1, parent2, i,j):
  # Create loop effect over array
  p1 = np.concatenate((parent1, parent1), axis=None)
  p2 = np.concatenate((parent2, parent2), axis=None)
  # Create empty child order
  child = np.full(len(parent2), None) 
  # Fill child with random selected sequence from parent1
  child[i:j] = p1[i:j]
  # Set pointers to the second crossover point in parent2 (jj) and child (ii)
  ii, jj = j, j
  # The recombination stops when all nodes in parent2 sequence have been added to the child
  while (jj < j + len(parent2)):
    if ii > len(parent2)-1:
      # when child's pointer reaches the end of the array go to position 0
      ii = 0
    if p2[jj] not in child: 
      # Missing nodes are added to the child
      child[ii] = p2[jj]
      ii += 1 # when added a new node, shift child's pointer to the left
    jj += 1
  return child

def selection(tsp, population):
  k = 5
  candidates = random.sample(population, k)
  fitnesses = [fitness(tsp, ind) for ind in candidates]
  selected = fitnesses.index(min(fitnesses))
  return candidates[selected]

def elimination(population, offspring, tsp):
  # λ+μ elimination
  print(sorted([(fitness(tsp, ind), ind) for ind in population], key=lambda ind: ind[0]))
  print(sorted([(fitness(tsp, ind), ind) for ind in offspring], key=lambda ind: ind[0]))
  combined = population + offspring
  ranked_individuals = sorted([(fitness(tsp, ind), ind) for ind in combined], key=lambda ind: ind[0])[0:len(population)]
  print(ranked_individuals)
  return [ind for fit, ind in ranked_individuals]

In [ ]:
tsp = TSP(5)
population=initialize(tsp,15)
for i in population:
  print("Candidate solution:  ", i.order)
  print("Objective value: ", fitness(tsp, i))

parent1 = selection(tsp, population)
parent2 = selection(tsp, population)
print(f'\n Selected parent {parent1.order} y fitness: {fitness(tsp, parent1)}')
print(f'\n Selected parent {parent2.order} y fitness: {fitness(tsp, parent2)}')

offspring = recombination(parent1, parent2)
print(f'\n Offspring recombination {offspring.order} y fitness: {fitness(tsp, offspring)}')

mutate(offspring)
print(f'\n Offspring mutated {offspring.order} y fitness: {fitness(tsp, offspring)}')

# Mutation
for ind in population:
  mutate(ind)    

off = [offspring]
# Elimination
population = elimination(population, off, tsp)
for i in population:
  print("Candidate solution:  ", i.order)
  print("Objective value: ", fitness(tsp, i))


In [21]:
# Only needed to import the file into colab, needs only to be run once
from google.colab import files
uploaded = files.upload()

filename = next(iter(uploaded))
matrix = np.genfromtxt(filename,delimiter=',')

tsp = TSP(matrix)

#print("Vertices:  ", tsp.vertices)
#print("Distance:  \n", tsp.distanceMatrix)

optimize(tsp)

"""best = elimination(pop, pop, tsp)
for i in best:
  print("Candidate solution:  ", i.order)
  print("Objective value: ", fitness(tsp, i))

fitnesses = [fitness(tsp, ind) for ind in best]
print("\nMean fitness:  ", statistics.mean(fitnesses))
print("Best fitness:  ", min(fitnesses))
"""

Saving tour29.csv to tour29 (10).csv

Mean fitness:   110263.81870147683
Best fitness:   71861.4266406352
[(71861.4266406352, <__main__.Individual object at 0x7fef7f2b54e0>), (76758.7609969751, <__main__.Individual object at 0x7fef7cbdb438>), (77626.45150705967, <__main__.Individual object at 0x7fef7f436e10>), (78925.7463019327, <__main__.Individual object at 0x7fef7d7ccba8>), (78925.7463019327, <__main__.Individual object at 0x7fef7d968a90>), (79372.70496586945, <__main__.Individual object at 0x7fef7d94add8>), (79930.43545498617, <__main__.Individual object at 0x7fef7f2a8358>), (81143.9847049865, <__main__.Individual object at 0x7fef7f2a8cc0>), (81190.6532113528, <__main__.Individual object at 0x7fef7f431240>), (81556.9354950081, <__main__.Individual object at 0x7fef7da01e80>), (83790.92287784361, <__main__.Individual object at 0x7fef7f2b5198>), (84211.83786424728, <__main__.Individual object at 0x7fef7f281d68>), (84696.91187851562, <__main__.Individual object at 0x7fef7f2b3940>), (84

IOPub data rate exceeded.
The notebook server will temporarily stop sending output
to the client in order to avoid crashing it.
To change this limit, set the config variable
`--NotebookApp.iopub_data_rate_limit`.

Current values:
NotebookApp.iopub_data_rate_limit=1000000.0 (bytes/sec)
NotebookApp.rate_limit_window=3.0 (secs)



[8 20 17 12 5 24 6 18 16 19 27 26 23 9 11 25 28 21 0 13 4 22 14 7 3 2 15 1
 10]
Candidate mutation probability:   0.05
Candidate solution:   [8 20 17 12 5 24 6 18 16 19 27 26 23 9 11 25 28 21 0 13 4 22 14 7 3 2 15 1
 10]
Candidate mutation probability:   0.05
Candidate solution:   [8 20 17 12 5 24 6 18 16 19 27 26 23 9 11 25 28 21 0 13 4 22 14 7 3 2 15 1
 10]
Candidate mutation probability:   0.05
Candidate solution:   [8 20 17 12 5 24 6 18 16 19 27 26 23 9 11 25 28 21 0 13 4 22 14 7 3 2 15 1
 10]
Candidate mutation probability:   0.05
Candidate solution:   [8 20 17 12 5 24 6 18 16 19 27 26 23 9 11 25 28 21 0 13 4 22 14 7 3 2 15 1
 10]
Candidate mutation probability:   0.05
Candidate solution:   [8 20 17 12 5 24 6 18 16 19 27 26 23 9 11 25 28 21 0 13 4 22 14 7 3 2 15 1
 10]
Candidate mutation probability:   0.05
Candidate solution:   [8 20 17 12 5 24 6 18 16 19 27 26 23 9 11 25 28 21 0 13 4 22 14 7 3 2 15 1
 10]
Candidate mutation probability:   0.05
Candidate solution:   [8 20 17 12 5

'best = elimination(pop, pop, tsp)\nfor i in best:\n  print("Candidate solution:  ", i.order)\n  print("Objective value: ", fitness(tsp, i))\n\nfitnesses = [fitness(tsp, ind) for ind in best]\nprint("\nMean fitness:  ", statistics.mean(fitnesses))\nprint("Best fitness:  ", min(fitnesses))\n'